## An example workflow

In [ ]:
#to use the full width of the browser window uncomment the code below and execute the cell
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [ ]:
from pyPoseidon.model import *
from pyPoseidon.dem import *
from pyPoseidon.meteo import *
import datetime
from pyPoseidon.utils.data import *

In [ ]:
import holoviews as hv
import geoviews as gv
import geoviews.feature as gf
from cartopy import crs


hv.notebook_extension('bokeh')

In [ ]:
#define in a dictionary the properties of the model..
dic={'minlon':160., # lat/lon window
     'maxlon':179.,
     'minlat':-49.,
     'maxlat':-33.,
     'solver':'d3d',
     'resolution':0.2, #grid resoltuion 
     'step':20, # step for output of map field in d3d
     'start_date':'2013-10-28',
     'time_frame':'2d',
     'ncores': 4 , #number of cores
     'rpath':'/Users/brey/Downloads/test/', #location of calc folder
     'conda_env':'mpi2' # optional conda env for running the solver
    }

### Create model

In [ ]:
#initialize a model
b = model(**dic)

### set it up

In [ ]:
b.set() #set it up 

### output to rpath 

In [ ]:
#set the run by saving the files
b.output()

In [ ]:
# save model info for further use
b.save()

In [ ]:
# save all matrices for further use
#b.pickle(path=path)

### execute

In [ ]:
#execute
b.run()

### Visualise

In [ ]:
otp = data([dic['rpath']])

In [ ]:
fig = plt.figure(figsize=(12,8))
ax = plt.subplot(projection=ccrs.PlateCarree());

otp.dem.bathymetry.plot.pcolormesh('longitude', 'latitude', ax=ax);

gp = ax.scatter(otp.grid.lons, otp.grid.lats, s=2, color='k',  label='grid points', transform=ccrs.PlateCarree());

pp = ax.scatter(otp.xh, otp.yh, s=2, color='b', label='pressure points', transform=ccrs.PlateCarree());

ax.legend()

ax.coastlines('50m'); ax.gridlines(draw_labels=True);

In [ ]:
otp.ds.S1[10,:,:].T.plot() # note the transpose

#### Holoviews

In [ ]:
#Fast but no map
%%opts Image [width=1050 height=650] (cmap='jet')
otp.hview('S1').to(hv.Image, ['longitude','latitude'], 'S1').hist()

#### Geoviews

In [ ]:
#Slow and heavy on resources but with map and zooming 
g50 = gv.feature.coastline(plot=dict(scale='50m'), style=dict(linewidth=1.5))

%%opts Image [colorbar=True width=1050 height=650 toolbar="above"  tools=['hover']] (cmap='viridis')
otp.gview('S1').to(gv.Image, ['longitude','latitude'], 'S1') * g50 * gf.borders()

#### Inherent Animation option

In [16]:
# relatively fast and 
otp.frames('S1',title='SSH')